## Simple demonstration of calculating segmentation metrics

In [1]:
import os
import sys
sys.path.append('..')
import umetrics
import filecmp 
import csv
import matplotlib.pyplot as plt
import numpy as np
from skimage.io import imread, imsave
import pandas as pd

## Set the data path

In [2]:
p = '/Users/nathanday/lowe_lab/fucci/set1/metrics/' 

p_man = '/Users/nathanday/lowe_lab/fucci/set1/singlecell_labels_manual'
p_mod = '/Users/nathanday/lowe_lab/fucci/set1/singlecell_labels_model'

cellid_list = ['1a', '1b', '2a', '2b', '3a', '3b', '4', '5' ]

#print('Input Cell ID')
"""cellid = 'cell'+ input()
results_path = os.path.join(p,'results') #,'results.csv')
try:
    # Create target Directory
    os.mkdir(results_path)
    print("Directory " , results_path ,  " Created ") 
except FileExistsError:
    print("Directory " , results_path ,  " already exists")
results_csv = os.path.join(results_path, cellid+'_results.csv')
image_results_path = os.path.join(results_path,cellid+ '_iou_image_output')
try:
    # Create target Directory
    os.mkdir(image_results_path)
    print("Directory " , image_results_path ,  " Created ") 
except FileExistsError:
    print("Directory " , image_results_path ,  " already exists")"""
    


'cellid = \'cell\'+ input()\nresults_path = os.path.join(p,\'results\') #,\'results.csv\')\ntry:\n    # Create target Directory\n    os.mkdir(results_path)\n    print("Directory " , results_path ,  " Created ") \nexcept FileExistsError:\n    print("Directory " , results_path ,  " already exists")\nresults_csv = os.path.join(results_path, cellid+\'_results.csv\')\nimage_results_path = os.path.join(results_path,cellid+ \'_iou_image_output\')\ntry:\n    # Create target Directory\n    os.mkdir(image_results_path)\n    print("Directory " , image_results_path ,  " Created ") \nexcept FileExistsError:\n    print("Directory " , image_results_path ,  " already exists")'

## load a single ground truth - prediction image pair

In [3]:
""" n = 1
    p = '/home/nathan/analysis/fucci/working_dir/t179_t684_crop/set1'
    true = imread(os.path.join(p, 'manual_labels', f'{n}_mask.modified.tif'))
    pred = imread(os.path.join(p, 'model_labels', f'{n}_mask.modified.tif'))"""

" n = 1\n    p = '/home/nathan/analysis/fucci/working_dir/t179_t684_crop/set1'\n    true = imread(os.path.join(p, 'manual_labels', f'{n}_mask.modified.tif'))\n    pred = imread(os.path.join(p, 'model_labels', f'{n}_mask.modified.tif'))"

## load a series of ground truth - prediction image pairs with the ability to save out images and results into csv

In [4]:
    #manual_labels = os.path.join(p, 'manual_labels')
    #model_labels = os.path.join(p, 'model_labels')
cellid_list = ['1b', '2a', '2b', '3a', '3b', '4', '5']
for m in cellid_list:
        cellid = 'cell'+m
        print(cellid)
        results_path = os.path.join(p,'results') #,'results.csv')
        try:
            # Create target Directory
            os.mkdir(results_path)
            print("Directory " , results_path ,  " Created ") 
        except FileExistsError:
            print("Directory " , results_path ,  " already exists")
        results_csv = os.path.join(results_path, cellid+'_results.csv')
        image_results_path = os.path.join(results_path,cellid+ '_iou_image_output')
        try:
            # Create target Directory
            os.mkdir(image_results_path)
            print("Directory " , image_results_path ,  " Created ") 
        except FileExistsError:
            print("Directory " , image_results_path ,  " already exists")  

        manual_labels = os.path.join(p_man, 'labels_' + cellid)
        model_labels = os.path.join(p_mod, 'labels_' + cellid)

        manual_mask_files = [f for f in os.listdir(manual_labels) if f.endswith('modified.tif')]
        manual_mask_files.sort(key = lambda f: int(f[0:4])) #sorts files numerically
        model_mask_files = [f for f in os.listdir(model_labels) if f.endswith('modified.tif')]   
        model_mask_files.sort(key = lambda f: int(f[0:4])) 

        if len(model_mask_files) != len(manual_mask_files):
            print('You have an unequal number of images for comparison, sort it out please')
            print('Manual labels:',(len(manual_mask_files)))
            print('Model labels:',(len(model_mask_files)))

            dc = filecmp.dircmp(manual_labels, model_labels) #.report()
            print("Missing files from model_mask_files:", dc.left_only)
            print("Missing files from manual_mask_files:", dc.right_only)

        i = 0 
        df = pd.DataFrame([], index=[i], columns=['Frame','IoU', 'localization_error', 'pixel_identity', 'n_true_labels','n_predicted_labels'])

        for i, n in enumerate(model_mask_files): #todo combine model/manual_mask_files lists 
            #p = '/home/nathan/analysis/fucci/working_dir/t179_t684_crop/set1'
            #true = imread(os.path.join(p, 'manual_labels', f'{n}'))
            #pred = imread(os.path.join(p, 'model_labels', f'{n}'))
            true = imread(os.path.join(manual_labels, f'{n}'))
            pred = imread(os.path.join(model_labels, f'{n}'))

            result = umetrics.calculate(true, pred)
            #result.plot()

            image_output = os.path.join(image_results_path, 'image_{}.png'.format(i)) #IMAGE OUTPUT BLOCK
            plt.savefig(image_output, bbox_to_inches='tight')
            plt.show()
            plt.close()
            print('')
            print(f'{n}')
            print(result.results)

            df.loc[i, 'Frame'] = i
            df.loc[i,'IoU'] = result.per_object_IoU
            df.loc[i,'localization_error'] = result.per_object_localization_error 
            df.loc[i,'pixel_identity'] = result.per_image_pixel_identity
            df.loc[i,'n_true_labels'] = result.n_true_labels 
            df.loc[i,'n_predicted_labels'] = result.n_pred_labels
            df.to_csv(results_csv, index=False) #need to figure out way to remove [] from output

cell1b
Directory  /Users/nathanday/lowe_lab/fucci/set1/metrics/results  already exists
Directory  /Users/nathanday/lowe_lab/fucci/set1/metrics/results/cell1b_iou_image_output  already exists
You have an unequal number of images for comparison, sort it out please
Manual labels: 1093
Model labels: 1091
Missing files from model_mask_files: ['0250_mask.tif.modified.tif', '0575_mask.tif.modified.tif']
Missing files from manual_mask_files: []


<Figure size 432x288 with 0 Axes>


0000_mask.tif.modified.tif
 Segmentation Metrics (n=1)
n_true_labels: 1
n_pred_labels: 1
n_true_positives: 1
n_false_positives: 0
n_false_negatives: 0
IoU: 1.000
Jaccard: 1.000
pixel_identity: 1.000
localization_error: 0.000



<Figure size 432x288 with 0 Axes>


0001_mask.tif.modified.tif
 Segmentation Metrics (n=1)
n_true_labels: 1
n_pred_labels: 1
n_true_positives: 1
n_false_positives: 0
n_false_negatives: 0
IoU: 1.000
Jaccard: 1.000
pixel_identity: 1.000
localization_error: 0.000



...


1090_mask.tif.modified.tif
 Segmentation Metrics (n=1)
n_true_labels: 1
n_pred_labels: 1
n_true_positives: 1
n_false_positives: 0
n_false_negatives: 0
IoU: 0.944
Jaccard: 1.000
pixel_identity: 1.000
localization_error: 4.844



<Figure size 432x288 with 0 Axes>


1091_mask.tif.modified.tif
 Segmentation Metrics (n=1)
n_true_labels: 1
n_pred_labels: 1
n_true_positives: 1
n_false_positives: 0
n_false_negatives: 0
IoU: 0.915
Jaccard: 1.000
pixel_identity: 0.999
localization_error: 9.550



<Figure size 432x288 with 0 Axes>


1092_mask.tif.modified.tif
 Segmentation Metrics (n=1)
n_true_labels: 1
n_pred_labels: 1
n_true_positives: 1
n_false_positives: 0
n_false_negatives: 0
IoU: 0.932
Jaccard: 1.000
pixel_identity: 1.000
localization_error: 7.516



In [5]:
#result = umetrics.calculate(true, pred)

## visualize the metrics

In [6]:
# uncomment for interactive
# %matplotlib qt

In [7]:
#print(result.results)

## plot some stats

In [8]:
import matplotlib.pyplot as plt

In [9]:
"""bins = np.linspace(0,3000,21)

plt.figure()
plt.hist(result._reference.areas, bins, alpha=0.5, label='true')
plt.hist(result._predicted.areas, bins, alpha=0.5, label='pred', edgecolor='k')
plt.legend()
plt.title('Histogram of detected object areas')
plt.xlabel('Pixels')
plt.show()"""

"bins = np.linspace(0,3000,21)\n\nplt.figure()\nplt.hist(result._reference.areas, bins, alpha=0.5, label='true')\nplt.hist(result._predicted.areas, bins, alpha=0.5, label='pred', edgecolor='k')\nplt.legend()\nplt.title('Histogram of detected object areas')\nplt.xlabel('Pixels')\nplt.show()"

## do some batch processing

In [10]:

files = []
model_labels = os.path.join(p, 'model_labels')
model_mask_files = [f for f in os.listdir(model_labels) if f.endswith('modified.tif')]   

for i, n in enumerate(model_mask_files):
    true = imread(os.path.join(p, 'manual_labels', f'{n}'))
    pred = imread(os.path.join(p, 'model_labels', f'{n}'))
    files.append((true, pred))

In [11]:
batch_result = umetrics.batch(files)

[[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 ...
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]


OSError: Cannot understand given URI: array([[0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, ....

In [ ]:
print(batch_result)

*NOTE(arl)*: the metrics here are calculated as follows in batch mode:
+ `n_true_labels` is the sum of all true labels, etc
+ `IoU` is the mean IoU of all found objects
+ `Jaccard` is the Jaccard index over all found objects
+ `localization_error` is the mean error for all found objects
+ `pixel_identity` is the per image pixel identity

In [ ]:
plt.figure()
plt.hist(batch_result.per_object_IoU)
plt.title('Histogram of per object IoU metric')
plt.xlabel('IoU')
plt.show()

In [ ]:
plt.figure()
plt.hist(batch_result.per_object_localization_error, bins=np.linspace(0,10,50))
plt.title('Histogram of per object localization error')
plt.xlabel('Error in Pixels')
plt.show()